### Threading

In [22]:
import threading

def printer(num):
    print(num)

for i in range(5):
    t = threading.Thread(target=printer, args=(i,))
    t.start()

01

2
3
4


In [21]:
my_lock = threading.Lock()

def printer(num):
    with my_lock:
        print(num)

for i in range(5):
    t = threading.Thread(target=printer, args=(i,))
    t.start()

0
1
2
3
4


In [35]:
import concurrent.futures

my_lock = threading.Lock()
def printer(num):
    with my_lock:
        print(num)
    return num

with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
    results = executor.map(printer, range(10))

0
1
3
4
2
5
6
7
8
9


In [33]:
list(results)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]

In [29]:
import concurrent.futures

my_lock = threading.Lock()
def printer(num1, num2):
    with my_lock:
        print(num1, num2)
    return num1

with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
    results = executor.map(printer, range(5), range(4,-1,-1))

0 4
1 3
2 2
3 1
4 0


In [30]:
list(results)

[0, 1, 2, 3, 4]

### Multiprocessing

In [ ]:
# !!! will not run in the notebook !!!

# import multiprocessing

# def printer(num):
#     print(num)
    
# with multiprocessing.Pool() as pool:
#     pool.map(printer, range(5))

In [36]:
script = """
import multiprocessing

def square(num):
    return num * num
    
if __name__ == '__main__':
    __spec__ = None    
    with multiprocessing.Pool(5) as pool:
        result = pool.map(square, range(5))
        print(result)
"""

with open('test-multiprocessing.py','w') as f:
    f.write(script)

%run test-multiprocessing.py

[0, 1, 4, 9, 16]


In [37]:
import concurrent.futures
import multiprocessing as mp
import time

def dummy(num):
    time.sleep(5)
    return num ** 2

start_time = time.time()
with concurrent.futures.ProcessPoolExecutor(max_workers=5, mp_context=mp.get_context('fork')) as executor:
    results = executor.map(dummy, range(10))
print("Total Time:", time.time() - start_time)

Total Time: 10.03440523147583


In [ ]:
for r in results:
    print(r)

### Comparing single-thread, multi-thread, and asyncio

[Example by J. Anderson](https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program)

In [38]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import requests
import time

def download_site(url, session):
    with session.get(url) as response:
        # print(f"Read {len(response.content)} from {url}")
        pass

def download_all_sites(sites):
    with requests.Session() as session:
        for url in sites:
            download_site(url, session)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    download_all_sites(sites)
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} in {duration} seconds")

Downloaded 160 in 6.636908769607544 seconds


In [39]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import concurrent.futures
import requests
import threading
import time

thread_local = threading.local()

def get_session():
    if not hasattr(thread_local, "session"):
        thread_local.session = requests.Session()
    return thread_local.session

def download_site(url):
    session = get_session()
    with session.get(url) as response:
        # print(f"Read {len(response.content)} from {url}")
        pass

def download_all_sites(sites):
    with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
        executor.map(download_site, sites)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    download_all_sites(sites)
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} in {duration} seconds")

Downloaded 160 in 1.5313899517059326 seconds


In [40]:
# !pip install nest_asyncio
import nest_asyncio

nest_asyncio.apply()

In [41]:
# https://realpython.com/python-concurrency/#how-to-speed-up-an-io-bound-program

import asyncio
import time
import aiohttp

async def download_site(session, url):
    async with session.get(url) as response:
        # print("Read {0} from {1}".format(response.content_length, url))
        pass

async def download_all_sites(sites):
    async with aiohttp.ClientSession() as session:
        tasks = []
        for url in sites:
            task = asyncio.ensure_future(download_site(session, url))
            tasks.append(task)
        await asyncio.gather(*tasks, return_exceptions=True)

if __name__ == "__main__":
    sites = [
        "https://www.jython.org",
        "http://olympus.realpython.org/dice",
    ] * 80
    start_time = time.time()
    asyncio.get_event_loop().run_until_complete(download_all_sites(sites))
    duration = time.time() - start_time
    print(f"Downloaded {len(sites)} sites in {duration} seconds")

Downloaded 160 sites in 0.2766399383544922 seconds


In [42]:
# this is not a function call, creates a coroutine object!
download_site("foo", "bar")

<coroutine object download_site at 0x1109b5230>